폐렴 X-ray 공개 데이터셋을 활용하여 폐렴 여부를 분류하는 딥러닝 모델을 생성/학습/평가하고, 그 결과를 비교해보자.

실습 목표

 * 영상 데이터를 불러오는 방법을 안다.
 * 딥러닝 모델의 층을 쌓는 방법을 안다.
 * 모델을 학습하는 방법과 학습한 모델을 평가하는 방법을 안다.
 * 이론으로 배운 개념이 어디에 적용되는지 확인한다.

목차

 * I. 입출력 데이터 처리
   1. 데이터 세트 불러오기
   2. 데이터 전처리
     1. 데이터 크기 조정하기
     2. 데이터 셔플
 * II. 커스텀 모델 학습 및 평가
   5. 모델 빌드 및 컴파일
   6. 모델 학습
   7. 모델 평가
 * III. CNN 모델 학습 및 평가
   5. 모델 빌드 및 컴파일
   6. 모델 학습
   7. 모델 평가

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
import os, random

import numpy as np
from tqdm import tqdm

import __________.______ as plt
import _______ as sns
import cv2 # opencv

import __________ as tf

In [ ]:
random.seed(42)
np.random.seed(42)
tf.random.set_seed(42)

In [ ]:
# 데이터 저장 경로
DATA_DIR = '/content/drive/MyDrive/chest_xray'

# 클래스 정보
labels = ['NORMAL', 'PNEUMONIA']

# I. 입출력 데이터 처리

## 1. 데이터 세트 불러오기

폐렴 환자와 정상인으로부터 수집한 X선 이미지 (출처: [kaggle](https://www.kaggle.com/datasets/paultimothymooney/chest-xray-pneumonia))

### 1) 데이터 하나만 읽어보기

데이터 경로 설정

In [ ]:
__._______(os.path.join(DATA_DIR, 'val', 'PNEUMONIA'))[:5]

In [ ]:
data_path = os.path.join(DATA_DIR, 'val', 'PNEUMONIA', ______________)
data_path

이미지 읽기

In [ ]:
img = ___.______(data_path)
img._____, img.min(), img.max()

이미지 데이터는 어떻게 생겼을까?

In [ ]:
___

이미지 데이터를 더블클릭했을 때처럼 보고 싶은데?

In [ ]:
___.______(img)
plt.show()

세균성 폐렴 환자의 폐 X선 영상은 이렇게 생겼구나!!

### 2) 활용할 수 있는 이미지를 모두 읽어서 변수에 저장하기

In [ ]:
def get_data(dataset_dir):
    
    imgs = []
    diagnosis = []


    for label in labels:
        data_path = os.path.join(dataset_dir, label)
        i = 0
        for file in tqdm(os.listdir(data_path)):
            if file.endswith('jpeg'):
                if i >= 600:
                    break
                else:    
                    # 이미지 읽기
                    img = cv2.imread(os.path.join(data_path, file))

                    # 이미지와 이미지에 대한 레이블 저장
                    imgs.append(img)
                    diagnosis.append(label)
                    i += 1

    return imgs, diagnosis

In [ ]:
img_train, diagnosis_train = get_data(os.path.join(DATA_DIR, 'train'))
img_val, diagnosis_val = get_data(os.path.join(DATA_DIR, 'val'))
img_test, diagnosis_test = get_data(os.path.join(DATA_DIR, 'test'))

len(img_train), len(diagnosis_train), len(img_val), len(diagnosis_val), len(img_test), len(diagnosis_test)

img_{dataset}에는 폐영상을, diagnosis_{dataset}에는 폐렴/정상에 대한 정보를 리스트 형태로 저장함. 학습/검증/평가 데이터 세트에는 폐렴/정상 데이터가 몇 개씩 있을지 확인해보자.

In [ ]:
np.unique(diagnosis_train, return_counts=True),\
np.unique(diagnosis_val, return_counts=True),\
np.unique(diagnosis_test, return_counts=True)

데이터 세트에 따른 폐렴과 정상 환자의 이미지 개수는?

### 3) 데이터 시각화

In [ ]:
print(img_train[0].shape)
___.______(img_train[0])
plt._____(diagnosis_train[0])
plt.show()

데이터 세트의 데이터를 하나씩 꺼내와서 시각화하고, 어떤 환자인지, 이미지의 크기는 어떤지 같이 확인해보자

In [ ]:
plt.figure(figsize=(8, 10))
plt.subplot(321), plt.imshow(img_train[0]), plt.title(f'{diagnosis_train[0]}, shape: {img_train[0].shape}')
plt.subplot(322), plt.imshow(img_train[-1]), plt.title(f'{diagnosis_train[-1]}, shape: {img_train[-1].shape}')
plt.subplot(323), plt.imshow(img_val[0]), plt.title(f'{diagnosis_val[0]}, shape: {img_val[0].shape}')
plt.subplot(324), plt.imshow(img_val[-1]), plt.title(f'{diagnosis_val[-1]}, shape: {img_val[-1].shape}')
plt.subplot(325), plt.imshow(img_test[0]), plt.title(f'{diagnosis_test[0]}, shape: {img_test[0].shape}')
plt.subplot(326), plt.imshow(img_test[-1]), plt.title(f'{diagnosis_test[-1]}, shape: {img_test[-1].shape}')
plt.show()

첫째 줄이 학습 데이터 세트, 둘째 줄이 검증 데이터 세트, 셋째 줄이 평가 데이터 세트인데, 데이터마다 크기와 비율이 제각각임을 알 수 있음

## 2. 데이터 전처리

### 1). 데이터 크기 조정

위 shape과 시각화 결과를 통해 데이터마다 크기가 다름을 확인함. 인공지능의 입력 데이터는 같은 크기를 가져야 함. 따라서 단일한 크기로 조정함. 영상의 크기는 다양하게 조절 가능한데, 오늘은 원활한 학습을 위해 작은 크기로 줄임

In [ ]:
IMG_SHAPE = (224, 224, 3)

데이터 크기 조정해보기

In [ ]:
print(img_train[0].shape)
___.______(img_train[0])
plt.show()

In [ ]:
resized_img = ___.______(img_train[0], dsize=IMG_SHAPE)
print(resized_img.shape)
___.______(resized_img)
plt.show()

`cv2.resize(img, dsize)` 메서드를 사용하여 이미지의 크기를 원하는 크기로 조정할 수 있음. `interpolation=`은 영상의 크기를 조절하는 방식을 지정하는 파라미터로, 이미지의 크기를 줄일 때에는 주로 영역보간법(`INTER_AREA`)을 활용함

In [ ]:
img_train = np.array([cv2.resize(img, dsize=IMG_SHAPE[:2], interpolation=cv2.INTER_AREA) for img in tqdm(img_train)])
img_val = np.array([cv2.resize(img, dsize=IMG_SHAPE[:2], interpolation=cv2.INTER_AREA) for img in tqdm(img_val)])
img_test = np.array([cv2.resize(img, dsize=IMG_SHAPE[:2], interpolation=cv2.INTER_AREA) for img in tqdm(img_test)])

img_train.shape, img_val.shape, img_test.shape

In [ ]:
diagnosis_train = np.array(diagnosis_train)
diagnosis_val = np.array(diagnosis_val)
diagnosis_test = np.array(diagnosis_test)

diagnosis_train.shape, diagnosis_val.shape, diagnosis_test.shape

In [ ]:
img_train.shape, diagnosis_train.shape

### 2) 데이터 셔플

현재 모든 데이터 세트의 데이터는 클래스 순서대로 구성됨. 이러한 데이터로 학습 시 모델에 편향이 발생할 수 있음. 데이터를 무작위로 섞는 셔플을 적용하여, 데이터에 있는 순서를 제거하자.

In [ ]:
diagnosis_train#, diagnosis_val, diagnosis_test

In [ ]:
def shuffle_data(imgs, diagnosis):
    
    # 인덱스 셔플
    shuffled_index = np.random.choice(diagnosis.shape[0], diagnosis.shape[0], replace=False) #np.random.shuffle(index)
    
    # 데이터 셔플
    shuffled_imgs = imgs[shuffled_index]
    shuffled_diagnosis = diagnosis[shuffled_index]
    
    return shuffled_imgs, shuffled_diagnosis

In [ ]:
img_train, diagnosis_train = shuffle_data(img_train, diagnosis_train)
img_val, diagnosis_val = shuffle_data(img_val, diagnosis_val)
img_test, diagnosis_test = shuffle_data(img_test, diagnosis_test)

In [ ]:
diagnosis_train

### 3) 전처리가 끝난 데이터는?

In [ ]:
img_train._____, diagnosis_train._____

In [ ]:
img_val._____, diagnosis_val._____

In [ ]:
img_test._____, diagnosis_test._____

# II. 커스텀 모델 학습 및 평가

## 5. 커스텀 모델 빌드 및 컴파일

학습할 모델을 쌓고(빌드), 쌓은 모델의 학습에 사용할 loss function, optimizer를 지정하여 컴파일한다.

### 1) 커스텀 모델 빌드

In [ ]:
def build_custom_model(input_shape):
    model = tf.keras.Sequential()
    model.add(tf.keras.layers.Flatten(input_shape=input_shape[:2]))
    model.add(tf.keras.layers.Dense(____, activation='relu'))
    model.add(tf.keras.layers.Dense(__, activation='relu'))
    model.add(tf.keras.layers.Dense(1, activation=______)) # 분류 문제

    return model

In [ ]:
model = build_custom_model(IMG_SHAPE)
model.______()

### 2) 커스텀 모델 컴파일

하이퍼 파라미터란?

In [ ]:
EPOCHS = 50
BATCH_SIZE = 30
LEARNING_RATE = 0.001

In [ ]:
# define optimizer
adam = tf.keras.optimizers.Adam(learning_rate=LEARNING_RATE)

# compile model
model.compile(optimizer=____,
             lloss='binary_crossentropy',
             metrics=['accuracy'],
             )

## 6. 모델 학습

### 1) 입출력 데이터 선언

In [ ]:
model.input

In [ ]:
img_train.shape, img_val.shape, img_test.shape

In [ ]:
X_train = np.array([x[:,:,0] for x in img_train])
X_val = np.array([x[:,:,0] for x in img_val])
X_test = np.array([x[:,:,0] for x in img_test])

X_train.shape, X_val.shape, X_test.shape

커스텀 모델의 입출력은 2차원 이미지임.

In [ ]:
y_train = np.squeeze(np.where(diagnosis_train == labels[0], 0, 1))
y_val = np.squeeze(np.where(diagnosis_val == labels[0], 0, 1))
y_test = np.squeeze(np.where(diagnosis_test == labels[0], 0, 1))

y_train.shape, y_val.shape, y_test.shape, y_train[0]

### 2) 모델 학습

In [ ]:
# model training

history = model.___(
    X_train, y_train,
    epochs=EPOCHS,
    validation_data=(X_val, y_val),
    batch_size=BATCH_SIZE,
)

### 3) Learning curve 확인하기

학습이 잘 수행되었다면, 실제 데이터와 예측 결과 데이터의 손실이 학습이 진행됨에 따라 줄어들어야 함.

In [ ]:
plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.title('custom model - learning curve')
plt.show()

## 7. 모델 평가하기

모델이 잘 만들어졌는지 평가 데이터로 확인

### 1) 정확도 계산하기

학습이 잘 수행되었는지 확인하기 위해서는 평가 데이터를 통해 정확도를 계산해야 함. 정확도는 다음과 같음.

> Accuracy(%) = (제대로 예측된 데이터의 개수) / (전체 데이터 개수) * 100

In [ ]:
test_loss, test_acc = model.________(______, ______, verbose=1)
val_loss, val_acc = model.________(______, ______, verbose=1)
train_loss, train_acc = model.________(______, ______, verbose=1)

### 2) 혼동 행렬(Confusion Matrix) 나타내기

혼동 행렬은 지도 학습으로 훈련된 분류 알고리즘의 성능을 시각화하는 방법으로, 모델이 예측을 잘 수행하였는지를 파악할 수 있다.

In [ ]:
y_pred = model.predict(X_test)
y_pred.shape, y_pred[0]

예측 결과를 차트로 그려보자

In [ ]:
plt.hist(y_pred)
plt.show()

시그모이드 함수를 사용하였으므로, 결과가 0~1 사이의 값으로 나옴. 0.5보다 작으면 0, 크면 1로 변환하여 맞췄는지 틀렸는지를 확인해보자

In [ ]:
y_pred = np.squeeze([int(x >= 0.5) for x in np.squeeze(_____)])
y_pred.shape, y_pred[0]

In [ ]:
from sklearn.metrics import _________________

cm = _________________(______, ______)

plt.figure(figsize=(6, 4))
sns.heatmap(cm, annot=True, fmt='d')
plt.xticks([0.5, 1.5], labels)
plt.yticks([0.5, 1.5], labels)
plt.xlabel("Predicted label")
plt.ylabel("True label")
plt.title("Confustion Matrix")
plt.show()

# III. CNN 모델 학습 및 평가 (DenseNet121)

## 5. 모델 빌드 및 컴파일

학습할 모델을 쌓고(빌드), 쌓은 모델의 학습에 사용할 loss function, optimizer를 지정하여 컴파일한다.

### 1) DenseNet121 아키텍처 파인 튜닝 (fine tuning)

In [ ]:
def build_pretrained_densenet121_model(input_shape):
    
    # architecture construction
    ### based on DenseNet121
    ### pretrained by imagenet

    # load basemodel
    baseModel = tf.keras.applications.densenet.DenseNet121(
        include_top=False,
        weights='imagenet',
        input_shape=input_shape,
        pooling='avg',
    )

    # construct the head of the model that will be placed on top of the base model
    headModel = tf.keras.layers.Dropout(0.5)(baseModel.output)
    headModel = tf.keras.layers.Dense(1, activation="sigmoid")(headModel)

    # place the head FC model on top of the base model
    model = tf.keras.Model(inputs=baseModel.input, outputs=headModel)

    return model

In [ ]:
model = build_pretrained_densenet121_model(IMG_SHAPE)
model.summary()

### 2) 모델 컴파일

In [ ]:
EPOCHS = 50
BATCH_SIZE = 30
LEARNING_RATE = 0.00001

In [ ]:
# define optimizer
adam = tf.keras.optimizers.Adam(learning_rate=LEARNING_RATE)

# compile model
model.compile(optimizer=adam,
             loss='binary_crossentropy',
             metrics=['accuracy'],
             )

## 6. 모델 학습

### 1) 입출력 데이터 선언

In [ ]:
model.input

CNN 모델의 입력은 3D 이미지임

In [ ]:
X_train, X_val, X_test = img_train, img_val, img_test

X_train.shape, X_val.shape, X_test.shape

In [ ]:
y_train = np.squeeze(np.where(diagnosis_train == labels[0], 0, 1))
y_val = np.squeeze(np.where(diagnosis_val == labels[0], 0, 1))
y_test = np.squeeze(np.where(diagnosis_test == labels[0], 0, 1))

y_train.shape, y_val.shape, y_test.shape, y_train[0]

### 2) 모델 학습

하이퍼 파라미터 설정

`model.fit()`을 통해 모델 학습을 수행할 수 있음

In [ ]:
# model training

history = model.fit(
    X_train, y_train,
    epochs=EPOCHS,
    validation_data=(X_val, y_val),
    batch_size=BATCH_SIZE,
)

### 3) Learning curve 확인하기

학습이 잘 수행되었다면, 실제 데이터와 예측 결과 데이터의 손실이 학습이 진행됨에 따라 줄어들어야 함.

In [ ]:
plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.title('cnn model - learning curve')
plt.show()

## 7. 모델 평가하기

모델이 잘 만들어졌는지 평가 데이터로 확인

### 1) 정확도 계산하기

학습이 잘 수행되었는지 확인하기 위해서는 평가 데이터를 통해 정확도를 계산해야 함. 정확도는 다음과 같음.

> Accuracy(%) = (제대로 예측된 데이터의 개수) / (전체 데이터 개수) * 100

In [ ]:
model.evaluate(X_test, y_test, verbose=1)
model.evaluate(X_val, y_val, verbose=1)
model.evaluate(X_train, y_train, verbose=1)

학습하지 않은 데이터에 대해서도 약 82%의 정확도로 폐렴을 잘 알아맞추는 것을 알 수 있음.

### 2) 혼동 행렬(Confusion Matrix) 나타내기

In [ ]:
y_pred = model.predict(X_test)
y_pred.shape, y_pred[0]

In [ ]:
y_pred = np.squeeze([int(x >= 0.5) for x in np.squeeze(y_pred)])
y_pred.shape, y_pred[0]

In [ ]:
from sklearn.metrics import confusion_matrix

cm = confusion_matrix(y_test, y_pred)

plt.figure(figsize=(6, 4))
sns.heatmap(cm, annot=True, fmt='d')
plt.xticks([0.5, 1.5], labels)
plt.yticks([0.5, 1.5], labels)
plt.xlabel("Predicted label")
plt.ylabel("True label")
plt.title("Confustion Matrix")
plt.show()

# 마무리
 * Q. 직접 만든 모델의 성능과 영상 처리 특화 모델의 성능은 어떻게 다른가요?
 * Q. 성능이 높으면 좋은 모델이라고 할 수 있을까요?

실습 목표

 * 영상 데이터를 불러오는 방법을 안다. => `cv2.imread()`
 * 딥러닝 모델의 층을 쌓는 방법을 안다. => `model.add([layers])`
 * 모델을 학습하는 방법과 학습한 모델을 평가하는 방법을 안다. => `model.fit()`, `model.evaluate()`
 * 이론으로 배운 개념이 어디에 적용되는지 확인한다. => node, layer, activation, optimizer, loss function, loss, learning_rate 등...


우리는 오늘..
 * 폐렴 X-ray 공개 데이터셋을 활용하여
 * 폐렴 여부를 분류하는
 * 딥러닝 모델을 만들고 학습하고 평가하였으며,
 * 영상 처리에 탁월한 성능을 보이는 딥러닝 모델과의 성능 차이를 확인함